In [1]:
import torch
from collections import defaultdict
import numpy as np
import mcubes
import trimesh

# from models.rendering import *
from models.rendering_shadows import * # render_rays, efficient_sm}}

from models.nerf import *

from datasets import dataset_dict
from dotmap import DotMap


from utils import load_ckpt
torch.cuda.is_available()

False

# Load model and data

In [3]:
# Change here #
img_wh = (128, 128) # full resolution of the input images
dataset_name = 'efficient_sm' # blender or llff (own data)
# ./eff_sm_updated_light_matrix/logs/128x128_single_image_grad_on_sm2_sigma_run3_2gpu/
scene_name = 'cuboid' # whatever you want
# the folder containing data
root_dir = '/home/gridsan/ktiwary/datasets/volumetric/results_500_v2_distance_transform_150/' 
# the model path

# ckpt_path = "./eff_sm_updated_light_matrix_NEW/ckpts/64x64_resulst_500v2_vase_sigma0_on_sm2_2gpu/epoch=13.ckpt"

"""
# ckpt_path = './eff_sm_updated_light_matrix_NEW/ckpts/128x128_sigma100_bunny_grad_on_sm2_sigma_run1_2gpu_interactive/'
# ckpt_path = '../nerf_pl-dev/ckpts/opacity_loss_64x64_nimp128_box_fov50_nosigma_randominit/epoch=44.ckpt' 
# ckpt_path = "../nerf_pl-dev/ckpts/opacity_loss_64x64_nimp128_run1_cont/epoch=45.ckpt"
# ckpt_path = "../nerf_pl/old_exps/logs_rgb_eff_sm_old/ckpts/legos/128x128_Nimp64_LN32_grad_on_bluroff/epoch=11.ckpt"
ckpt_path = "../nerf_pl/old_exps/eff_sm_updated_light_matrix_old/ckpts/sigma/128x128_Nimp64_LN32_sm2/epoch=0.ckpt"
ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW/ckpts/64x64_sigma10_bunny_grad_on_sm2_sigma_run1_2gpu_interactive/epoch=13.ckpt"
# ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW/ckpts/SINGLE_IMAGE_128x128_sigma10_bunny_grad_on_sm2_sigma_run1_2gpu_interactive/epoch=45.ckpt"
ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW/ckpts/128_sigma50_vasepruned_grad_on_sm2_sigma_run1_2gpu/epoch=10.ckpt"
# ckpt_path = "../nerf_pl-dev/ckpts/BOX_SIGMA30_128x128_sm2_smapper2d/epoch=234.ckpt"
# ckpt_path = "../nerf_pl-dev/ckpts/BUNNY_SIGMA10_128x128_sm2_smapper2d_run2_random_init/epoch=228.ckpt"
ckpt_path = "../nerf_pl-dev/ckpts/128x128_sm2_smapper2d_nimp128_nsamp64_sigma/epoch=419.ckpt"
ckpt_path = "../nerf_pl-dev/ckpts/64x64_sm2_smapper2d_nimp128_nsamp64_sigma/epoch=50.ckpt"
ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW/ckpts/64_sigma50_singler137_vasepruned_grad_on_sm2_run1_2gpu/epoch=20.ckpt"
ckpt_path = "./logs-eval/NEW___SIGMA_Nimp_64_64x64_grad_on_light_LN_32_shadowmethod2/epoch=10.ckpt"


ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW/ckpts/CUBOID_BASELINE_64_sigma150_gradon/epoch=2.ckpt"
ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW/ckpts/64_sigma10_vasepruned_gradon_sm2_halffov/epoch=95.ckpt"


ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW/ckpts/128_sigma50_vasepruned_grad_on_sm2_sigma_run1_2gpu/epoch=24.ckpt"
ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW/ckpts/64_sigma50_vase_gradon_sm2_halffov/epoch=76.ckpt"
ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW/ckpts/64_sigma100_vase_grad_on_sm2_run2_2gpu/epoch=3.ckpt"

ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW/ckpts/128_sigma50_vasepruned_grad_on_sm2_sigma_run1_2gpu/epoch=99.ckpt"

ckpt_path = "../nerf_pl-dev/ckpts/128_sigma50_vase_varcam_pruned_normalfov/epoch=238.ckpt"
ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW/ckpts/64x64_resulst_500v2_vase_sigma150_on_sm2_2gpu/epoch=3.ckpt"
# chairs path 
"""


ckpt_path = '../nerf_pl-dev/ckpts/128x128_sm2_smapper2d_nimp128_nsamp64_sigma/epoch=461.ckpt'


###############
hparams = {
    'black_and_white_test': False, 
    'coords_trans': False, 
    'blur': -1, 
    'white_pix': -1, 
}
hparams = DotMap(hparams)
kwargs = {'root_dir': root_dir,
          'img_wh': img_wh, 
         'hparams': hparams}
    
chunk = 1024*32
# dataset = dataset_dict[dataset_name](**kwargs)

embedding_xyz = Embedding(3, 10)
embedding_dir = Embedding(3, 4)

# ckpt_path = "./eff_sm_updated_light_matrix_NEW/ckpts/128x128_resulst_500v2_vase_sigma150_on_sm2_run2_2gpu/epoch=19.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW/ckpts/128x128_resulst_500v2_vase_sigma150_on_sm2_run2_2gpu/epoch=24.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/VASE_SIGMA150_64x64_sm2_nimp128_nsamp64_run1/epoch=279.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/VASE_SIGMA150_to_0_64x64_sm2_nimp128_nsamp64_run1/epoch=350.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/BUNNY_SIGMA150_scratch_64x64_sm2_nimp128_nsamp64_run1/epoch=291.ckpt"

# ckpt_path = "./eff_sm_updated_light_matrix_NEW/ckpts/128x128_resulst_500v2_vase_sigma150_on_sm2_run2_2gpu/epoch=30.ckpt"
# ckpt_path = "./logs_rgb_eff_sm/ckpts/sigma/vasev2_500_sigma_150_grad_on_light_sm2run2/epoch=199.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW/ckpts/128x128_resulst_500v2_vase_sigma150_on_sm2_run2_2gpu/epoch=30.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW/ckpts/BUNNYsigma150_128x128_results500v2_grad_on_sm2_run1_2gpu/"


# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/BUNNY_SIGMA_50_from150_scratch_64x64_sm2_nimp128_nsamp64_run1/epoch=397.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW/ckpts/128x128_resulst_500v2_vase_sigma150_on_sm2_2gpu/epoch=2.ckpt"

# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/VASE_SIGMA150_128x128_sm2_nimp128_nsamp64_run1/epoch=37.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/BUNNY_SIGMA_50_from150_scratch_64x64_sm2_nimp128_nsamp64_run1/epoch=444.ckpt"
# ckpt_path = "././eff_sm_updated_light_matrix_NEW_feb20/ckpts/64x64_results_500_v2_scratch_sigma0_gradon_run3_2gpu/epoch=80.ckpt"


# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/VASE_SIGMA150_128x128_sm2_nimp128_nsamp64_run1/epoch=48.ckpt"

# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/LOWER_PRES_VASE_SIGMA150_64x64_sm2_nimp128_nsamp128_run1/epoch=33.ckpt"

# ckpt_path = "/home/gridsan/ktiwary/cameraculture_shared/tzofi/nerf_pl/eff_sm_updated_light_matrix_NEW_feb20/ckpts/SPHERE_SIGMA150_64x64_sm2_nimp128_nsamp64_run1/epoch=80.ckpt"
# ckpt_path = "/home/gridsan/ktiwary/cameraculture_shared/tzofi/nerf_pl/eff_sm_updated_light_matrix_NEW_feb20/ckpts/VW_SIGMA150_64x64_sm2_nimp128_nsamp64_run1/epoch=17.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/SPHERE_SIGMA150_64x64_sm2_nimp128_nsamp64_run1/epoch=292.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/RAY_TERM_ONLY_VASE_SIGMA150_64x64_sm2_nimp128_nsamp64_run1/epoch=294.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/RAY_TERM_ONLY_LOWER_PRES_VASE_SIGMA150_64x64_sm2_nimp128_nsamp128_run1/epoch=95.ckpt"

# ckpt_path = "../nerf_pl-dev/RTD/ckpts/ray_term_dist_BUNNY_SIGMA100_64x64_sm2_smapper2d_nimp128_nsamp64/epoch=16.ckpt"
# ckpt_path = "../nerf_pl-dev/RTD/ckpts/ray_term_dist_BUNNY_SIGMA100_128x128_sm2_smapper2d/epoch=58.ckpt"



# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/VASE_SIGMA150_128x128_sm2_nimp128_nsamp64_run1/epoch=128.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/VW_SIGMA150_64x64_sm2_nimp128_nsamp64_run1/epoch=295.ckpt"

# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/SPHERE_SIGMA_50_64x64_sm2_nimp128_nsamp64_run1/epoch=298.ckpt"

# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/SPHERE_SIGMA_50_to_0_64x64_sm2_nimp128_nsamp64_run1/epoch=304.ckpt"
# ckpt_path = "/home/gridsan/ktiwary/cameraculture_shared/tzofi/nerf_pl/eff_sm_updated_light_matrix_NEW_feb20/ckpts/64x64_results_500_v2_64Vase_sigma150to50to0_e499/epoch=506.ckpt"

# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/LOWER_PRES_VASE_SIGMA150_64x64_sm2_nimp128_nsamp128_run1/epoch=73.ckpt"

# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/VASE_SIGMA150_128x128_sm2_nimp128_nsamp64_run1/epoch=128.ckpt"

# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb27/ckpts/statue_200_sigma150_64x64_sm2_nimp128_nsamp64_run1/epoch=295.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb27/ckpts/statue_800_sigma_50_64x64_sm2_nimp128_nsamp64_run1/epoch=283.ckpt"


ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/VW_SIGMA150_64x64_sm2_nimp128_nsamp64_run1/epoch=295.ckpt"
# kinda works vase checkpoint 

### this one!! 
### this one!! 
### this one!! 
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/RAY_TERM_ONLY_VASE_SIGMA150_64x64_sm2_nimp128_nsamp64_run1/epoch=294.ckpt"
### this one!! 
### this one!! 
### this one!! 


# ckpt_path = "./eff_sm_updated_light_matrix_NEW/ckpts/64x64_resulst_500v2_vase_sigma0_on_sm2_2gpu/epoch=15.ckpt"
# ckpt_path = "./logs_rgb_eff_sm/ckpts/sigma/vasev2_500_sigma_150_grad_on_light_sm2run2/epoch=199.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW/ckpts/64x64_resulst_500v2_vase_sigma0_on_sm2_2gpu/epoch=9.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/64x64_results_500_v2_64Vase_sigma150to50_e279/epoch=298.ckpt"

# (final for figure)
# ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW_feb20/ckpts/64x64_results_500_v2_64Vase_sigma150to50_e279/epoch=499.ckpt"

# ckpt_path = "../nerf_pl/eff_sm_updated_light_matrix_NEW_feb20/ckpts/64x64_results_500_v2_64Vase_sigma150to50_e55/epoch=298.ckpt"

# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/64x64_results_500_v2_64Vase_sigma150to50_e55/epoch=298.ckpt"


# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb27/ckpts/statue_800_sigma_150_64x64_sm2_nimp128_nsamp64_run1/epoch=295.ckpt"
# # ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb27/ckpts/statue_800_sigma_50_64x64_sm2_nimp128_nsamp64_run1/epoch=283.ckpt"
# #### Good chairs 
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb27/ckpts/CHAIR_sigma150_var_cam_run1/epoch=49.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb27/ckpts/CHAIR_sigma150_var_cam_run1/epoch=236.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_mar02/ckpts/CHAIR_sigma_50_var_cam_run2_e52/epoch=284.ckpt"

# ckpt_path = "./eff_sm_updated_light_matrix_NEW_mar02/ckpts/UPDATED_LT_BUNNY_SIGMA150_scratch_run1/epoch=10.ckpt"
# ckpt_path = "/home/gridsan/ktiwary/cameraculture_shared/tzofi/nerf_pl/eff_sm_updated_light_matrix_NEW_mar02/ckpts/TripleCuboid_SIGMA150_64x64_sm2_nimp128_nsamp64_run1_new/"

# # shpere ok
# # ckpt_path = "./eff_sm_updated_light_matrix_NEW_mar02/ckpts/UPDATED_LT_SPHERE_SIGMA150_64x64_run3/epoch=7.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_mar02/ckpts/UPDATED_LT_SPHERE_SIGMA150_64x64_run3/epoch=8.ckpt"


# ckpt_path = "./eff_sm_updated_light_matrix_NEW_mar02/ckpts/CHAIR_sigma_50_var_cam_run2_e52/epoch=284.ckpt"

# ckpt_path = "./eff_sm_updated_light_matrix_NEW_mar02/ckpts/UPDATED_LT_BUNNY_SIGMA150_scratch_run1/epoch=299.ckpt"


# # good bunny 
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_mar02/ckpts/UPDATED_LT_BUNNY_SIGMA150_scratch_run1/epoch=299.ckpt"


# ckpt_path = "./eff_sm_updated_light_matrix_NEW_mar02/ckpts/UPDATED_LT_SPHERE_SIGMA_50_64x64_run1_e8/epoch=295.ckpt"



ckpt_path = "/home/gridsan/ktiwary/cameraculture_shared/tzofi/baseline_nerf/nerf_pl/ckpts/CUBOID_SIGMA_30_64x64_run1/epoch=282.ckpt"

ckpt_path = "/home/gridsan/ktiwary/cameraculture_shared/tzofi/baseline_nerf/nerf_pl/ckpts/VASE_SIGMA_50_64x64_run1/epoch=295.ckpt"
ckpt_path = "/home/gridsan/ktiwary/cameraculture_shared/tzofi/baseline_nerf/nerf_pl/ckpts/VASE_SIGMA_50_128x128_run2/epoch=1.ckpt"
ckpt_path = "./eff_sm_updated_light_matrix_NEW_mar02/ckpts/ECCV_sigma150_var_cam_run1/epoch=296.ckpt"


# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/64x64_results_500_v2_64Vase_sigma150to50_e279/epoch=499.ckpt"
####
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_mar02/ckpts/CHAIR_sigma150_var_cam_run1_nsamples128/epoch=2.ckpt"


    
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/LOWER_PRES_VASE_SIGMA150_64x64_sm2_nimp128_nsamp128_run1/epoch=33.ckpt"
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb20/ckpts/64x64_results_500_v2_64Vase_sigma150to50_e55/epoch=298.ckpt"




# Best Cuboid Paths (final for figure)
# ckpt_path = './eff_sm_updated_light_matrix/ckpts/128x128_single_image_grad_on_sm2_sigma_run3_2gpu/epoch=136.ckpt'
# ckpt_path = './eff_sm_updated_light_matrix/ckpts/128x128_single_image_grad_on_sm2_sigma_run3_2gpu/epoch=170.ckpt'
# ckpt_path = './eff_sm_updated_light_matrix/ckpts/128x128_single_image_grad_on_sm2_sigma_run3_2gpu/epoch=167.ckpt'



# epoch=91.ckpt' 
# ckpt_path = './eff_sm_updated_light_matrix/ckpts/128x128_single_image_grad_on_sm2_sigma_run2/epoch=18.ckpt'
# ckpt_path = './eff_sm_updated_light_matrix/ckpts/128x128_single_image_grad_on_sm2_sigma_run3_2gpu/epoch=77.ckpt'


# Statue of Liberty 
# ckpt_path = "./eff_sm_updated_light_matrix_NEW_feb27/ckpts/statue_800_sigma_50_64x64_sm2_nimp128_nsamp64_run1/epoch=283.ckpt"



nerf_fine = NeRF()
print("ckpt_path", ckpt_path)
load_ckpt(nerf_fine, ckpt_path, model_name='nerf_fine')
nerf_fine.eval() # .cuda().eval();
nerf_fine

ckpt_path ./eff_sm_updated_light_matrix_NEW_mar02/ckpts/ECCV_sigma150_var_cam_run1/epoch=296.ckpt


NeRF(
  (xyz_encoding_1): Sequential(
    (0): Linear(in_features=63, out_features=256, bias=True)
    (1): ReLU(inplace=True)
  )
  (xyz_encoding_2): Sequential(
    (0): Linear(in_features=256, out_features=256, bias=True)
    (1): ReLU(inplace=True)
  )
  (xyz_encoding_3): Sequential(
    (0): Linear(in_features=256, out_features=256, bias=True)
    (1): ReLU(inplace=True)
  )
  (xyz_encoding_4): Sequential(
    (0): Linear(in_features=256, out_features=256, bias=True)
    (1): ReLU(inplace=True)
  )
  (xyz_encoding_5): Sequential(
    (0): Linear(in_features=319, out_features=256, bias=True)
    (1): ReLU(inplace=True)
  )
  (xyz_encoding_6): Sequential(
    (0): Linear(in_features=256, out_features=256, bias=True)
    (1): ReLU(inplace=True)
  )
  (xyz_encoding_7): Sequential(
    (0): Linear(in_features=256, out_features=256, bias=True)
    (1): ReLU(inplace=True)
  )
  (xyz_encoding_8): Sequential(
    (0): Linear(in_features=256, out_features=256, bias=True)
    (1): ReLU(inpla

# Search for tight bounds of the object (trial and error!)

In [8]:
### Tune these parameters until the whole object lies tightly in range with little noise ###
N = 128 # controls the resolution, set this number small here because we're only finding
        # good ranges here, not yet for mesh reconstruction; we can set this number high
        # when it comes to final reconstruction.
min_ = -55. # chair is -35, 35
max_ =  55.
xmin, xmax = min_, max_ # -50, 50 # left/right range
# xmin, xmax = -25, 25 # min_, max_ # -50, 50 # left/right range


ymin, ymax = min_, max_  # forward/backward range
# ymin, ymax = -75, 25 #min_, max_  # forward/backward range


zmin, zmax = min_, max_ # up/down range
# zmin, zmax = -35, 35 # min_, max_ # up/down range


## Attention! the ranges MUST have the same length!
############################################################################################
x = np.linspace(xmin, xmax, N)
y = np.linspace(ymin, ymax, N)
z = np.linspace(zmin, zmax, N)

xyz_ = torch.FloatTensor(np.stack(np.meshgrid(x, y, z), -1).reshape(-1, 3))#.cuda()
dir_ = torch.zeros_like(xyz_)#.cuda()

with torch.no_grad():
    B = xyz_.shape[0]
    out_chunks = []
    for i in range(0, B, chunk):
        xyz_embedded = embedding_xyz(xyz_[i:i+chunk]) # (N, embed_xyz_channels)
        dir_embedded = embedding_dir(dir_[i:i+chunk]) # (N, embed_dir_channels)
        xyzdir_embedded = torch.cat([xyz_embedded, dir_embedded], 1)
#         print(xyzdir_embedded.shape)
#         raise
        out_chunks += [nerf_fine(xyzdir_embedded)]
    rgbsigma = torch.cat(out_chunks, 0)
    
sigma = rgbsigma[:, -1].cpu().numpy()
sigma = np.maximum(sigma, 0)
sigma = sigma.reshape(N, N, N)
sigma

array([[[3.5841316e-02, 3.8424067e-02, 3.8831148e-02, ...,
         3.8695810e-03, 1.9345174e-03, 1.7948390e-03],
        [3.4394018e-02, 3.6026552e-02, 3.6071207e-02, ...,
         3.1653999e-03, 1.0821307e-03, 7.7916775e-04],
        [3.5898544e-02, 3.7471551e-02, 3.7160017e-02, ...,
         3.3031651e-03, 1.9342129e-03, 1.2897504e-03],
        ...,
        [6.3984171e-02, 6.2901333e-02, 5.7170480e-02, ...,
         4.9297266e-02, 5.3758472e-02, 4.5367111e-02],
        [5.8660958e-02, 5.8104217e-02, 5.0271023e-02, ...,
         5.4878689e-02, 5.8544885e-02, 4.6604324e-02],
        [6.2953964e-02, 5.9906363e-02, 5.2503452e-02, ...,
         4.2438392e-02, 4.4696644e-02, 3.1029496e-02]],

       [[3.3502966e-02, 3.5705641e-02, 3.5764281e-02, ...,
         3.4434851e-03, 1.7768829e-03, 1.4241538e-03],
        [3.2177474e-02, 3.3798903e-02, 3.3379402e-02, ...,
         3.1686681e-03, 1.2790100e-03, 7.3785149e-04],
        [3.3415243e-02, 3.4934487e-02, 3.4731064e-02, ...,
         2.987

In [9]:
# print(sigma)
sigma_threshold = 0.00#1#005 # contPLY_PATHs the noise (lower=maybe more noise; higher=some mesh might be missing)
# The below lines are for visualization, COMMENT OUT once you find the best range and increase N!
vertices, triangles = mcubes.marching_cubes(sigma, sigma_threshold)
print(vertices.shape, triangles.shape)
mesh = trimesh.Trimesh(vertices/N, triangles)
mesh.show() #viewer='gl')

(147133, 3) (289744, 3)


In [230]:
ckpt_path

'/home/gridsan/ktiwary/cameraculture_shared/tzofi/baseline_nerf/nerf_pl/ckpts/CUBOID_SIGMA_30_64x64_run1/epoch=282.ckpt'

In [49]:
# # You can already export "colorless" mesh if you don't need color
# mcubes.export_mesh(vertices, triangles, "final_meshes/128x128_single_image_grad_on_sm2_sigma_run3_2gpu_e167.dae")
# mesh.show()

In [236]:
PLY_PATH = ckpt_path.split('/')[-2] + ckpt_path.split('/')[-1][-4:] +'.ply'
PLY_PATH = "./final_meshes/BASELINE_CUBOID_SIGMA_30_64x64_run1_epoch282.ply"

result = trimesh.exchange.ply.export_ply(mesh, encoding='ascii')
output_file = open(PLY_PATH, "wb+")
output_file.write(result)
output_file.close()

KeyboardInterrupt: 

In [58]:
import open3d as o3d
from open3d import JVisualizer


ImportError: cannot import name 'JVisualizer' from 'open3d' (/home/gridsan/ktiwary/.conda/envs/nerf_pl/lib/python3.7/site-packages/open3d/__init__.py)

In [57]:
# armadillo_mesh = o3d.data.ArmadilloMesh()
# mesh = o3d.io.read_triangle_mesh(PLY_PATH)

pcd = o3d.io.read_point_cloud(PLY_PATH)
print(pcd)
print(np.asarray(pcd.points))
o3d.visualization.draw_geometries([pcd])


PointCloud with 221950 points.
[[0.        0.        0.1484375]
 [0.        0.        0.234375 ]
 [0.        0.        0.1015625]
 ...
 [0.7421875 0.7421875 0.4921875]
 [0.7421875 0.7421875 0.421875 ]
 [0.7421875 0.7421875 0.453125 ]]
[Open3D WARNING] GLFW Error: GLX: No GLXFBConfigs returned
[Open3D WARNING] GLFW Error: GLX: Failed to find a suitable GLXFBConfig
[Open3D WARNING] Failed to create window
[Open3D WARNING] [DrawGeometries] Failed creating OpenGL window.


# Extract colored mesh

Once you find the best range, now **RESTART** the notebook, and copy the configs to the following cell
and execute it.

In [ ]:
# Copy the variables you have above here! ####
img_wh = (800, 800) # full resolution of the input images
dataset_name = 'blender' # blender or llff (own data)
scene_name = 'lego' # whatever you want
root_dir = '/home/ubuntu/data/nerf_example_data/nerf_synthetic/lego/' # the folder containing data
ckpt_path = 'ckpts/exp2/epoch=05.ckpt' # the model path

N = 128 # controls the resolution, set this number small here because we're only finding
        # good ranges here, not yet for mesh reconstruction; we can set this number high
        # when it comes to final reconstruction.
xmin, xmax = -1.2, 1.2 # left/right range
ymin, ymax = -1.2, 1.2 # forward/backward range
zmin, zmax = -1.2, 1.2 # up/down range
sigma_threshold = 50. # controls the noise (lower=maybe more noise; higher=some mesh might be missing)
###############################################

import os
os.environ['ROOT_DIR'] = root_dir
os.environ['DATASET_NAME'] = dataset_name
os.environ['SCENE_NAME'] = scene_name
os.environ['IMG_SIZE'] = f"{img_wh[0]} {img_wh[1]}"
os.environ['CKPT_PATH'] = ckpt_path
os.environ['N_GRID'] = "256" # final resolution. You can set this number high to preserve more details
os.environ['X_RANGE'] = f"{xmin} {xmax}"
os.environ['Y_RANGE'] = f"{ymin} {ymax}"
os.environ['Z_RANGE'] = f"{zmin} {zmax}"
os.environ['SIGMA_THRESHOLD'] = str(sigma_threshold)
os.environ['OCC_THRESHOLD'] = "0.2" # probably doesn't require tuning. If you find the color is not close
                                    # to real, try to set this number smaller (the effect of this number
                                    # is explained in my youtube video)

!python extract_color_mesh.py \
    --root_dir $ROOT_DIR \
    --dataset_name $DATASET_NAME \
    --scene_name $SCENE_NAME \
    --img_wh $IMG_SIZE \
    --ckpt_path $CKPT_PATH \
    --N_grid $N_GRID \
    --x_range $X_RANGE \
    --y_range $Y_RANGE \
    --z_range $Z_RANGE \
    --sigma_threshold $SIGMA_THRESHOLD \
    --occ_threshold $OCC_THRESHOLD

In [175]:
trans_t = lambda t : torch.Tensor([
    [1,0,0,0],
    [0,1,0,0],
    [0,0,1,t],
    [0,0,0,1]]).float()

rot_phi = lambda phi : torch.Tensor([
    [1,0,0,0],
    [0,np.cos(phi),-np.sin(phi),0],
    [0,np.sin(phi), np.cos(phi),0],
    [0,0,0,1]]).float()

rot_theta = lambda th : torch.Tensor([
    [np.cos(th),0,-np.sin(th),0],
    [0,1,0,0],
    [np.sin(th),0, np.cos(th),0],
    [0,0,0,1]]).float()


def pose_spherical(theta, phi, radius):
    c2w = trans_t(radius)
    c2w = rot_phi(phi/180.*np.pi) @ c2w
    c2w = rot_theta(theta/180.*np.pi) @ c2w
    c2w = torch.Tensor(np.array([[-1,0,0,0],[0,0,1,0],[0,1,0,0],[0,0,0,1]])) @ c2w
    return c2w

# Extract Spherical Poses

In [176]:
from models.camera import Camera
from datasets.ray_utils import *

render_poses = torch.stack([pose_spherical(angle, -60., 100.0) for angle in np.linspace(-180,180,40+1)[:-1]], 0)

In [1]:
camera_angle_x = 0.5 * np.pi
h, w = 128, 128
import importlib
# del datasets
import datasets
importlib.reload(datasets)
all_ppc = []
root_dir = '/home/gridsan/ktiwary/datasets/volumetric/results_500_v2_distance_transform_150/' 
hparams = {
    'black_and_white_test': False, 
    'coords_trans': False, 
    'blur': -1, 
    'white_pix': -1, 
}
hparams = DotMap(hparams)
kwargs = {'root_dir': root_dir,
          'img_wh': img_wh, 
         'hparams': hparams}

dataset = datasets.dataset_dict[dataset_name](**kwargs)


NameError: name 'np' is not defined

In [2]:
for p in range(render_poses.shape[0]):
    c2w = render_poses[p][:3, :4]
    print(c2w)
    hfov = camera_angle_x * 180./np.pi
    ppc = Camera(hfov, (h, w))
    ppc.set_pose_using_blender_matrix(c2w, False)
    all_ppc.extend([ppc]*h*w)
    rays_o, rays_d = get_rays(dataset.directions, c2w)
    rays = torch.cat([rays_o, rays_d, 
                      self.near*torch.ones_like(rays_o[:, :1]),
                      self.far*torch.ones_like(rays_o[:, :1])],
                      1) # (H*W, 8)

    with torch.no_grad():
        B = xyz_.shape[0]
        out_chunks = []
        for i in range(0, B, chunk):
            xyz_embedded = embedding_xyz(xyz_[i:i+chunk]) # (N, embed_xyz_channels)
            dir_embedded = embedding_dir(dir_[i:i+chunk]) # (N, embed_dir_channels)
            xyzdir_embedded = torch.cat([xyz_embedded, dir_embedded], 1)
    #         print(xyzdir_embedded.shape)
    #         raise
            out_chunks += [nerf_fine(xyzdir_embedded)]
        rgbsigma = torch.cat(out_chunks, 0)

    sigma = rgbsigma[:, -1].cpu().numpy()



NameError: name 'render_poses' is not defined